# Append UUID to SHA256 CSV

In [15]:
from os.path import join
from pathlib import Path
import difflib

from tqdm import tqdm_notebook as tqdm
import pandas as pd
import dask.dataframe as dd
import numpy as np

In [2]:
# names
DATA_STORE_NAS = '/data_store_nas/'
dir_dataset = 'datasets/people/vgg_face2/metadata'

In [25]:
# associate each file with an identity
fp_index = join(DATA_STORE_NAS, dir_dataset, 'index.csv')
df_index = pd.read_csv(fp_index).set_index('index')
df_index['identity'] = [-1] * len(df_index)
df_index.head(2)

sha256  identity
index                                                             
0      a39a1df855cb0c70dc553c5e9afa35b4f7c00f4011ca10...        -1
1      e360f93613baa68cede6731d2603873cdabd3993841cfd...        -1

In [26]:
# get file info
fp_files = join(DATA_STORE_NAS, dir_dataset, 'files.csv')
df_files = pd.read_csv(fp_files).set_index('index')
print(len(df_files))
df_files.head()

3311286


ext       fn        subdir
index                            
0      jpg  0089_01  test/n006211
1      jpg  0168_01  test/n006211
2      jpg  0213_01  test/n006211
3      jpg  0010_01  test/n006211
4      jpg  0115_01  test/n006211

In [27]:
fp_identities = join(DATA_STORE_NAS, dir_dataset, 'identities.csv')
df_identities = dd.read_csv(fp_identities).set_index('index')
print(len(df_identities))
df_identities.head(2)

9131


class_id                 description gender  images             name
index                                                                     
0      n000001                  Dalai Lama      m     424  14th Dalai Lama
1      n000002  American singer-songwriter      f     315    A Fine Frenzy

In [28]:
class_ids = {}
for row in df_identities.itertuples():
  class_id = row.class_id
  index = row.Index
  if class_id not in class_ids.keys():
    class_ids[class_id] = index

In [31]:
for row in tqdm(df_index.itertuples(), total=len(df_index)):
  file_index = row.Index
  file_row = df_files.iloc[file_index]
  subdir = file_row['subdir']
  class_id = subdir.split('/')[1]
  identity_index = class_ids[class_id]
  df_index.at[row.Index, 'identity'] = identity_index

In [34]:
fp_index_new = join(DATA_STORE_NAS, dir_dataset, 'index_new.csv')
df_index.to_csv(fp_index_new)

In [30]:
df_index.head()

sha256  identity
index                                                             
0      a39a1df855cb0c70dc553c5e9afa35b4f7c00f4011ca10...      6123
1      e360f93613baa68cede6731d2603873cdabd3993841cfd...      6123
2      3920a8bdf523a5bf7da9258ec414a741462d0cfbec8d2c...      6123
3      577ce218e4a61e612942c55fd172cac4b48becacbfc708...      6123
4      b27d37425a4e59dc4d37c3df331d0b69e4919338a3d46f...      6123